Polaris Injector Calcs (v2)

In this program we will calculate all the parameters necessary to design an unlike impinging triplet injector.

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import math

First off, we need to know the mass flow rates of the oxidizer (nitrous oxide) and fuel (ethanol). Our total mass flow rate is 1.3 kg/s. However, our fuel to oxidizer ratio is 1:4.5, so we need a lot more oxidizer mass flow rate than fuel. We will distribute the flow rate by having two orifices for oxidizer and one orifice for fuel per triplet group. To obtain the ratios of mass flow rates, we can simply multiply the total mass flow by each ratio, accounting for the fact that there are 3 orifices per group and 5 groups in total.

In [4]:
mdot_nitrous_total = 1.3 * (4.5/5.5)
mdot_ethanol_total = 1.3 * (1/5.5)

mdot_nitrous = mdot_nitrous_total / 10
mdot_ethanol = mdot_ethanol_total / 5

print("mdot_ox: ", mdot_nitrous)
print("mdot_ethanol: ", mdot_ethanol)

mdot_ox:  0.10636363636363637
mdot_ethanol:  0.04727272727272728


Here are some other necessary parameters: c_d is the discharge coefficient, which was calculated in a MATLAB program run by Alex. It is the predicted ratio of actual discharge of mass at the end of the nozzle to ideal discharge of mass at the end of the nozzle.

rho_ethanol is the density of ethanol (789 kg/m^3).

rho_nitrous is the density of nitrous oxide (817 kg/m^3). pressure_chamber is the stagnation pressure of the chamber converted from 520 psi to Pa.

delta_pressure_injector is the pressure drop across the injector in Pa (converted from 100 psi), should be 15-20% of the chamber pressure.

pressure_fuel_inlet is the pressure in the fuel manifold.

pressure_oxidizer_inlet is the pressure in the oxidizer manifold.

d_ox is the diameter of the oxidier holes in inches.

d_fuel is the diameter of the fuel holes in inches.

v_nitrous is the exit velocity from the oxidizer orifices. Calculated via Bernoulli's principle

v_ethanol is the exit velocity from the fuel orifices. Calculated via Bernoulli's principle.

In [5]:
c_d = 0.41
rho_ethanol = 789
rho_nitrous = 817
pressure_chamber = 460*6895
delta_pressure_injector = 97*6895
pressure_fuel_inlet = delta_pressure_injector + pressure_chamber
pressure_oxidizer_inlet = delta_pressure_injector + pressure_chamber
d_ox = 7/64
d_fuel = 1/16
v_nitrous = np.sqrt((2*delta_pressure_injector)/rho_nitrous)
v_ethanol = np.sqrt((2*delta_pressure_injector)/rho_ethanol)
print("v_nitrous: ", v_nitrous)
print("v_ethanol: ", v_ethanol)

v_nitrous:  40.4628968566491
v_ethanol:  41.17461041052858


Now let's define some helper functions to convert angles from deg to rad and vice versa.

In [6]:
def deg_to_rad(angle):
    """ Converts angle from deg to rad."""
    return angle*np.pi/180

def rad_to_deg(angle):
    """ Converts angle from rad to deg."""
    return angle*180/np.pi

The geometry of the V2 injector is significantly simplified compared to V1. The ethanol orifice will point straight down, and there will be one nitrous orifice on either side of the ethanol orifice, each at 30 degrees. This preserves the total 60 degrees recommended by JPL, and improves mixing efficiency compared to V1.

In [7]:
theta_nitrous = 30

Next, we define the distance between the ethanol orifice and one nitrous orifice (same on both sides), based on what fits in the geometry of the injector. Then, we verify that the impingement distance is greater than 5 times the average of the hole diameters for thermal safety of the faceplate. 

In [11]:
d_of = 0.38 # inches
impinge_d = d_of / np.tan(deg_to_rad(theta_nitrous)) # inches
impingement_safety = impinge_d / ((2*d_ox+d_fuel)/3)
print("This number should be greater than 5: ", impingement_safety)

This number should be greater than 5:  7.020579273345851


Next we want to calculate the height of the injector face. We choose an L/d ratio of 5 for both types of orifices, and from this we can calculate the height with trig.

In [12]:
L_ox = d_ox * 5
L_fuel = d_fuel * 5
h_ox = L_ox * np.cos(deg_to_rad(theta_nitrous)) # inches
h_fuel = L_fuel # inches
print("Height of faceplate for oxidizer: ", h_ox)
print("Height of faceplate for fuel: ", h_fuel)

Height of faceplate for oxidizer:  0.4736076426946149
Height of faceplate for fuel:  0.3125


Next, we get optimal cross-sectional area of each annulus, which is given by 4 * A_total where A_total is the total cross sectional area of the orifices for fuel/ox. Not sure where this relation comes from. Finally, given we calculate the y dimension of the cross-section of each annulus given the x dimension.

In [13]:
A_nitrous_total = np.pi*(d_ox/2)**2 * 10
A_ethanol_total = np.pi*(d_fuel/2)**2 * 5
A_ox_annulus = 4 * A_nitrous_total
A_fuel_annulus = 4 * A_ethanol_total

# only need to enter half x direction (i.e. one side of the cross section)
d_ox_annulus_x = float(input("Enter in a value for the x-component of oxidizer annulus cross-sectional area. It should be bigger than the distance between the oxidizer holes, and also be wide enough to fit a 1/4th inch pipe fitting: "))
d_fuel_annulus_x = float(input("Enter in a value for the x-component of fuel annulus cross-sectional area. It should be wide enough to fit a 1/16th inch pipe fitting: "))
d_ox_annulus_y = A_ox_annulus / d_ox_annulus_x / 2
d_fuel_annulus_y = A_fuel_annulus / d_fuel_annulus_x / 2

print(f'X component of oxidizer annulus: {d_ox_annulus_x}')
print(f'Y component of oxidizer annulus: {d_ox_annulus_y}')
print(f'X component of fuel annulus: {d_fuel_annulus_x}')
print(f'Y component of fuel annulus: {d_fuel_annulus_y}')

Enter in a value for the x-component of oxidizer annulus cross-sectional area. It should be bigger than the distance between the oxidizer holes, and also be wide enough to fit a 1/4th inch pipe fitting: 2.9948
Enter in a value for the x-component of fuel annulus cross-sectional area. It should be wide enough to fit a 1/16th inch pipe fitting: 0.25
X component of oxidizer annulus: 2.9948
Y component of oxidizer annulus: 0.06274630910778384
X component of fuel annulus: 0.25
Y component of fuel annulus: 0.1227184630308513


Next we need to calculate the distance from each orifice to the impingement point, which will then allow us to calculate the time to impingement for each stream.

In [14]:
d_impingement_nitrous = impinge_d / np.cos(deg_to_rad(theta_nitrous))
d_impingement_ethanol = impinge_d

t_nitrous = d_impingement_nitrous / v_nitrous
t_ethanol = d_impingement_ethanol / v_ethanol

The time for each stream to the impingement point cannot be the half period (or odd multiple of the half period) of the longitudinal mode of instability in the chamber (Huzel & Huang, pp. 148). The instability is dependent on the chamber length, so we can use this calculation to inform our decision on chamber length. We first need the speed of sound, which is given by sqrt(gammaRTc/M), which are all known parameters. We then calculate the frequency of instability modes, which is the speed of sound over twice the chamber length. After some algebra, we find that the chamber length should not be the numbers given below (or any odd multiple).

In [16]:
# Known parameters, SI units
gamma = 1.1589
R = 324.0271
Tc = 3028

# speed of sound in chamber
a_c = np.sqrt(gamma*R*Tc)

# chamber lengths to avoid, inches
L_avoid_1 = a_c * t_nitrous / 4 * 39.3701
L_avoid_2 = a_c * t_ethanol / 4 * 39.3701
print(f"Avoid these lengths and odd multiples: {L_avoid_1}, {L_avoid_2}")

Avoid these lengths and odd multiples: 197.1309118141685, 167.76943260247012


Next we will calculate the chances of cavitation when fluid is flowing through the orifice. Significant cavitation decreases mass flow rate and causes instabilities. We first want to calculate K, the cavitation number, which is given by (p_inlet - p_v)/(delta_pressure_injector) where p_inlet is the pressure in the manifold, p_v is the vapor pressure, and delta_pressure_injector is the pressure drop across the injector. K should be greater than 1.5 for moderate to low likelihood of cavitation. 

First we calculate p_v using the Clausius-Clapeyron Equation.

The vapor pressure of nitrous is 747 psi at 20 °C. The vapor pressure of ethanol is 0.86 psi at 20 °C. We will find p_v at the temperature of the manifold, which is the temperature of the fluids in the tank.

Heat of vaporization of nitrous is 4e3 J/mol, heat of vaporization of ethanol is 4.22e4 J/mol. (Hansen, Agbor, and Keil, 2007; Kretschmer and Wiebe, 1949).

In [20]:
R = 8.31 # gas constant
H_nitrous = 4e3
H_ethanol = 4.22e4
T_final = float(input("Enter the temperature in the manifold: "))+273 # C to K
T1 = 20+273
p_v1_nitrous = 747 # psi
p_v1_ethanol = 0.86

p_v_nitrous = p_v1_nitrous * math.e ** (H_nitrous/R * (1/T1-1/T_final))
p_v_ethanol = p_v1_ethanol * math.e ** (H_ethanol/R * (1/T1-1/T_final))

print("P_v of nitrous: ", p_v_nitrous)
print("P_v of ethanol: ", p_v_ethanol)

Enter the temperature in the manifold: 26.7
P_v of nitrous:  774.9447013197785
P_v of ethanol:  1.2669869031050405


Next we calculate the cavitation numbers for fuel and ox.

In [21]:
K_nitrous = (pressure_oxidizer_inlet-p_v_nitrous*6895)/delta_pressure_injector
K_ethanol = (pressure_fuel_inlet-p_v_ethanol*6895)/delta_pressure_injector

print("Nitrous cavitation number: ", K_nitrous)
print("Ethanol cavitation number: ", K_ethanol)

Nitrous cavitation number:  -2.246852590925551
Ethanol cavitation number:  5.729206320586545


Everything below here is for testing only.

In [22]:
pressure_chamber

3171700

In [45]:
G_hem = 3e4 # kg/(m^2*s)
G_spi = math.sqrt(2*rho_nitrous*delta_pressure_injector) # kg/(m^2*s)
# k = math.sqrt((delta_pressure_injector)/(p_v_nitrous*6895 - pressure_chamber))
t_b = math.sqrt(3/2 * rho_nitrous / (p_v_nitrous*6895-pressure_chamber))
t_r = L_ox * math.sqrt(rho_nitrous/(2*delta_pressure_injector))
k = t_b/t_r

G = c_d*(1/(1+k)*G_spi + (1-1/(1+k))*G_hem) # kg/(m^2*s)
mdot_from_G = G * np.pi*(d_ox/2)**2

print("k: ", k)
print(f"G_spi fraction: {1/(1+k)}, G_hem fraction: {1-1/(1+k)}")
print("G: ", G)
print("Calculated mdot: ", mdot_from_G)

k:  1.757685908918046
G_spi fraction: 0.3626228776693214, G_hem fraction: 0.6373771223306786
G:  12754.677073997773
Calculated mdot:  119.83825622158793
33058.18673188231
